In [3]:
import polars as pl
import os
from plotly.subplots import make_subplots
import plotly.graph_objects as go

import math

DATA_DIRECTORY = os.environ.get("DATA_DIRECTORY")
PICARRO_DATA_DIRECTORy = os.environ.get("PICARRO_DATA_DIRECTORY")

In [4]:
# 10m preprocessed acropolis data
df_acropolis = pl.read_parquet(os.path.join(DATA_DIRECTORY, "processed", "1h_sbs_acropolis.parquet"))

In [5]:
system_ids = df_acropolis["system_id"].unique().to_list()

In [6]:
def plot_acropolis_scatter(x_col_name, y_col_name="diff",max_col = 3, x_title="x_name", y_title="ACROPOLIS - Picarro (ppm)", title_text="title_name"):
    # fixed
    titles = []
    max_rows = math.ceil(len(system_ids)/max_col)

    for system_id in system_ids:
        titles.append(f"System: {int(system_id)}")
        
    fig = make_subplots(rows=max_rows, cols=max_col, shared_yaxes='all', subplot_titles=(titles), x_title=x_title, y_title=y_title)

    row = 1
    col = 0

    for system_id in system_ids:
        
        col += 1
        
        if col > max_col:
            col = 1
            row += 1

        #----
        df_plot = df_acropolis.filter(pl.col("system_id")==system_id) \
            .select(["creation_timestamp", y_col_name, x_col_name]) \
            
        l_delta = df_plot.select(y_col_name).to_series().to_list()
        l_humidity = df_plot.select(x_col_name).to_series().to_list()
        
        fig.add_trace(go.Scatter(x=l_humidity, y=l_delta, name = f"MC-{int(system_id)}", mode='markers'),row=row, col=col)

        
    fig.update_layout(title_text=title_text, height=1000, width=1000, showlegend=False)    
    fig.show()

In [7]:
df_acropolis.head(3)

shape: (3, 37)
┌───────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬──────────┬──────────┐
│ system_id ┆ sys_name_s ┆ creation_ ┆ system_na ┆ … ┆ diff      ┆ date      ┆ std      ┆ var      │
│ ---       ┆ hort       ┆ timestamp ┆ me        ┆   ┆ ---       ┆ ---       ┆ ---      ┆ ---      │
│ i64       ┆ ---        ┆ ---       ┆ ---       ┆   ┆ f64       ┆ date      ┆ f64      ┆ f64      │
│           ┆ str        ┆ datetime[ ┆ str       ┆   ┆           ┆           ┆          ┆          │
│           ┆            ┆ μs, UTC]  ┆           ┆   ┆           ┆           ┆          ┆          │
╞═══════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪══════════╪══════════╡
│ 1         ┆ acropolis- ┆ 2024-02-0 ┆ null      ┆ … ┆ -0.229331 ┆ 2024-02-0 ┆ 1.093883 ┆ 1.19658  │
│           ┆ 1          ┆ 7         ┆           ┆   ┆           ┆ 7         ┆          ┆          │
│           ┆            ┆ 00:00:00  ┆           ┆   ┆           ┆           ┆          ┆          │
│           ┆            ┆ UTC       ┆           ┆   ┆           ┆           ┆          ┆          │
│ 1         ┆ acropolis- ┆ 2024-02-0 ┆ null      ┆ … ┆ 0.072194  ┆ 2024-02-0 ┆ 1.227588 ┆ 1.506973 │
│           ┆ 1          ┆ 7         ┆           ┆   ┆           ┆ 7         ┆          ┆          │
│           ┆            ┆ 01:00:00  ┆           ┆   ┆           ┆           ┆          ┆          │
│           ┆            ┆ UTC       ┆           ┆   ┆           ┆           ┆          ┆          │
│ 1         ┆ acropolis- ┆ 2024-02-0 ┆ null      ┆ … ┆ 0.279841  ┆ 2024-02-0 ┆ 0.871461 ┆ 0.759444 │
│           ┆ 1          ┆ 7         ┆           ┆   ┆           ┆ 7         ┆          ┆          │
│           ┆            ┆ 02:00:00  ┆           ┆   ┆           ┆           ┆          ┆          │
│           ┆            ┆ UTC       ┆           ┆   ┆           ┆           ┆          ┆          │
└───────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴──────────┴──────────┘

In [8]:
# parameters
x_col_name = "gmp343_corrected"
y_col_name = "CO2_corr"
max_col = 3
x_title = "ACROPOLIS (ppm)"
y_title = "PICARRO (ppm)"
title_text = "Measured CO2 Concentration" 

plot_acropolis_scatter(x_col_name=x_col_name,y_col_name=y_col_name,max_col=max_col, x_title=x_title, y_title = y_title, title_text=title_text)

In [9]:
# parameters
x_col_name = "h2o_v%"
max_col = 3
x_title = "Absolute Humidity (ppm)"
title_text = "Scatter Plots: Delta CO2 vs Absolute Humidity" 

plot_acropolis_scatter(x_col_name=x_col_name,max_col=max_col, x_title=x_title, title_text=title_text)

In [10]:
# parameters
x_col_name = "gmp343_temperature"
max_col = 3
x_title = "Temperature (°C)"
title_text = "Scatter Plots: Delta CO2 vs Temperature" 

plot_acropolis_scatter(x_col_name=x_col_name,max_col=max_col, x_title=x_title, title_text=title_text)

In [11]:
# parameters
x_col_name = "bme280_pressure"
max_col = 3
x_title = "Pressure (mbar)"
title_text = "Scatter Plots: Delta CO2 vs Pressure" 

plot_acropolis_scatter(x_col_name=x_col_name,max_col=max_col, x_title=x_title, title_text=title_text)